In [1]:
#Importing all the necessary libraries
import nltk
import pandas as pd
import numpy as np
from nltk.corpus import stopwords
nltk.download("stopwords")
import re
from gensim.models import Word2Vec
from sklearn.model_selection import train_test_split
import pickle
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report

import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
from pathlib import Path
import os
import glob
import math
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


In [ ]:
# Extracting all the files.
file_graphics=os.listdir('/content/drive/MyDrive/IR assignment/A2_Q3/comp.graphics')
file_hockey=os.listdir('/content/drive/MyDrive/IR assignment/A2_Q3/rec.sport.hockey')
file_med=os.listdir('/content/drive/MyDrive/IR assignment/A2_Q3/sci.med')
file_space=os.listdir('/content/drive/MyDrive/IR assignment/A2_Q3/sci.space')
file_politics=os.listdir('/content/drive/MyDrive/IR assignment/A2_Q3/talk.politics.misc')


In [ ]:
# Creating a dictionary which contains all file names and their respective contents.
file_content_graphics={'class_label':[],'content':[]}
for i in file_graphics:
  file1 = open("/content/drive/MyDrive/IR assignment/A2_Q3/comp.graphics/"+i,"r",encoding='utf-8',errors='ignore')
  file_content_graphics['class_label'].append(1)
 # text = file1.read().decode(errors='replace')
  text=file1.read()
  file_content_graphics['content'].append(text)

In [ ]:
# Creating a dictionary which contains all file names and their respective contents.
file_content_hockey={'class_label':[],'content':[]}
for i in file_hockey:
  file1 = open("/content/drive/MyDrive/IR assignment/A2_Q3/rec.sport.hockey/"+i,"r",encoding='utf-8',errors='ignore')
  file_content_hockey['class_label'].append(2)
 # text = file1.read().decode(errors='replace')
  text=file1.read()
  file_content_hockey['content'].append(text)

In [ ]:
# Creating a dictionary which contains all file names and their respective contents.
file_content_med={'class_label':[],'content':[]}
for i in file_med:
  file1 = open("/content/drive/MyDrive/IR assignment/A2_Q3/sci.med/"+i,"r",encoding='utf-8',errors='ignore')
  file_content_med['class_label'].append(3)
 # text = file1.read().decode(errors='replace')
  text=file1.read()
  file_content_med['content'].append(text)

In [ ]:
# Creating a dictionary which contains all file names and their respective contents.
file_content_space={'class_label':[],'content':[]}
for i in file_space:
  file1 = open("/content/drive/MyDrive/IR assignment/A2_Q3/sci.space/"+i,"r",encoding='utf-8',errors='ignore')
  file_content_space['class_label'].append(4)
 # text = file1.read().decode(errors='replace')
  text=file1.read()
  file_content_space['content'].append(text)

In [ ]:
# Creating a dictionary which contains all file names and their respective contents.
file_content_politics={'class_label':[],'content':[]}
for i in file_politics:
  file1 = open("/content/drive/MyDrive/IR assignment/A2_Q3/talk.politics.misc/"+i,"r",encoding='utf-8',errors='ignore')
  file_content_politics['class_label'].append(5)
 # text = file1.read().decode(errors='replace')
  text=file1.read()
  file_content_politics['content'].append(text)

In [ ]:
#Creating the dataframes for each dictionary that we have created above.
file_c_1=pd.DataFrame({'content':file_content_graphics['content'],'label':file_content_graphics['class_label']})
file_c_2=pd.DataFrame({'content':file_content_hockey['content'],'label':file_content_hockey['class_label']})
file_c_3=pd.DataFrame({'content':file_content_med['content'],'label':file_content_med['class_label']})
file_c_4=pd.DataFrame({'content':file_content_space['content'],'label':file_content_space['class_label']})
file_c_5=pd.DataFrame({'content':file_content_politics['content'],'label':file_content_politics['class_label']})

In [ ]:
#Concatenation of all the dataframes
file_content=(pd.concat([file_c_1, file_c_2, file_c_3, file_c_4, file_c_5], ignore_index=True))

In [ ]:
#Saving the dataframe
#file_content.to_csv('/content/drive/MyDrive/IR assignment/A2/file_content_A2_Q3.csv',index=False)

In [2]:
#Reading the file_content dataframe which we have saved in the local storage
file_content=pd.read_csv('/content/drive/MyDrive/IR assignment/A2/file_content_A2_Q3.csv')

In [3]:
file_content

content  label
0     Newsgroups: comp.graphics\nPath: cantaloupe.sr...      1
1     Newsgroups: comp.graphics\nPath: cantaloupe.sr...      1
2     Xref: cantaloupe.srv.cs.cmu.edu comp.graphics....      1
3     Newsgroups: comp.graphics\nPath: cantaloupe.sr...      1
4     Newsgroups: comp.graphics\nPath: cantaloupe.sr...      1
...                                                 ...    ...
4995  Path: cantaloupe.srv.cs.cmu.edu!magnesium.club...      5
4996  Xref: cantaloupe.srv.cs.cmu.edu misc.legal:610...      5
4997  Xref: cantaloupe.srv.cs.cmu.edu alt.sex:111872...      5
4998  Path: cantaloupe.srv.cs.cmu.edu!crabapple.srv....      5
4999  Xref: cantaloupe.srv.cs.cmu.edu misc.legal:610...      5

[5000 rows x 2 columns]

**PART-1**

In [4]:
# Applying tokenization on text corpus.
w_token = nltk.tokenize.WhitespaceTokenizer()

In [ ]:
# Tokenization function
def tokenized_text(text):
    return w_token.tokenize(text)

In [ ]:
#Converted all the words in lower case.
file_content['content']=file_content['content'].str.lower()
#Removed all the special characters and punctuation marks.
file_content['content'] = file_content['content'].str.replace('[^a-zA-Z0-9]',' ')
file_content['content'] = file_content['content'].replace(r'http\S+', '', regex=True).replace(r'www\S+', '', regex=True)
stop_word = stopwords.words('english')
#Removed all the stopwords from the corpus using NLTK stopwords.
file_content['content'] = file_content['content'].apply(lambda x: ' '.join([word for word in x.split() if word not in (stop_word)]))
#Performed tokenization on the document corpus.
#Performed lemmatization on the tokens of the corpus.
file_content['content_tokens']=file_content.content.apply(tokenized_text)

In [ ]:
#Creating unique tokens list and token frequency dictionary.
token_frequency={}
unique_tokens_in_docs={}
# token_frequency stores the frequency of tokens of the document corpus.
unique_tokens=[]
# unique_tokens stores the list of unique tokes of the document corpus. 
for idx,rows in file_content.iterrows():
  tokens=rows.loc['content_tokens']
  label=rows['label']
  unique_tokens_in_docs[idx]=set()
  for word in tokens:
    unique_tokens_in_docs[idx].add(word)
    if(word in token_frequency.keys()):
        temp=token_frequency[word]
        if(label in temp.keys()):
          temp[label] += 1
        else:
          temp[label]=1
    else:
        token_frequency[word] = {}
        token_frequency[word][label]=1
        unique_tokens.append(word)

In [ ]:
unique_tokens_in_docs

{0: {'002',
  '02',
  '03',
  '11230',
  '13h',
  '192947',
  '1993',
  '1993apr17',
  '202844',
  '21',
  '22',
  '240282',
  '320x200',
  '3d',
  '56',
  '57',
  '61',
  '735364676',
  'across',
  'adamski',
  'ans',
  'apr',
  'article',
  'assembly',
  'au',
  'australia',
  'b5l',
  'c',
  'c5n3x0',
  'c5nf8t',
  'calling',
  'cantaloupe',
  'centre',
  'cmu',
  'com',
  'come',
  'comp',
  'computer',
  'copy',
  'course',
  'crabapple',
  'cs',
  'cso',
  'date',
  'draw',
  'drawer',
  'drawing',
  'ece',
  'ed',
  'edu',
  'eng',
  'enough',
  'europa',
  'fast',
  'fax',
  'fellow',
  'file',
  'fill',
  'fs7',
  'ftp',
  'game',
  'gmt',
  'graphics',
  'gsq',
  'gtefsd',
  'hi',
  'howland',
  'id',
  'information',
  'inline',
  'joseph',
  'keywords',
  'lines',
  'local',
  'looking',
  'lucas',
  'message',
  'mode',
  'mps',
  'msdos',
  'munnari',
  'needed',
  'net',
  'network',
  'news',
  'newsgroups',
  'newsroom',
  'ohio',
  'organization',
  'orourke',
  'ospr

In [ ]:
# Generating icf values for each tokens
icf_values={}
n=5
for i in unique_tokens:
  cf=len(token_frequency[i].keys())
  icf=math.log(n/(cf),2)
  icf_values[i]=icf

In [ ]:
token_frequency['file'].keys()

dict_keys([1, 2, 3, 4, 5])

In [ ]:
#Generating the tf-icf matrix for the dataset
matrix_tf_icf=np.zeros((file_content.shape[0],len(unique_tokens)))
value=1
for i in range(file_content.shape[0]):
  doc=unique_tokens_in_docs[i]
  tokens=list(doc)
  label=file_content.iloc[i,1]
  for word in tokens:
    tf=token_frequency[word][label]
    icf=icf_values[word]
    overall_score=tf*icf
    matrix_tf_icf[i,unique_tokens.index(word)]=overall_score

In [ ]:
matrix_tf_icf.shape

(5000, 68471)

In [ ]:
#Saving the matrix that we have created above
#np.save('/content/drive/MyDrive/IR assignment/A2/matrix_tf_icf.npy',matrix_tf_icf)

In [5]:
#Load the matrix from the local storage
matrix_tf_icf=np.load('/content/drive/MyDrive/IR assignment/A2/matrix_tf_icf.npy')

**Top-K Features**

In [6]:
def sum_in_blocks(a, c):
    l = c*(len(a)//c)
    return a[:l].reshape(-1,c,a.shape[1]).sum(1)

In [7]:
#Adding the features for each class for each tokens
top=sum_in_blocks(matrix_tf_icf, c=1000)

In [8]:
top

array([[0.00000000e+00, 7.62003801e+05, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 3.48648127e+02, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 2.83296724e+01, 0.00000000e+00, ...,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00],
       [0.00000000e+00, 5.15084952e+00, 0.00000000e+00, ...,
        2.32192809e+00, 2.32192809e+00, 2.32192809e+00]])

In [ ]:
top[0]

In [9]:
#Sort all the features for each class
top_k=top[0]
idx=list(range(matrix_tf_icf.shape[1]))
top_k=dict(zip(idx,top_k))
top_1_sorted=dict(sorted(top_k.items(), key=lambda item: item[1],reverse=True))

top_k=top[1]
idx=list(range(matrix_tf_icf.shape[1]))
top_k=dict(zip(idx,top_k))
top_2_sorted=dict(sorted(top_k.items(), key=lambda item: item[1],reverse=True))


top_k=top[2]
idx=list(range(matrix_tf_icf.shape[1]))
top_k=dict(zip(idx,top_k))
top_3_sorted=dict(sorted(top_k.items(), key=lambda item: item[1],reverse=True))


top_k=top[3]
idx=list(range(matrix_tf_icf.shape[1]))
top_k=dict(zip(idx,top_k))
top_4_sorted=dict(sorted(top_k.items(), key=lambda item: item[1],reverse=True))


top_k=top[4]
idx=list(range(matrix_tf_icf.shape[1]))
top_k=dict(zip(idx,top_k))
top_5_sorted=dict(sorted(top_k.items(), key=lambda item: item[1],reverse=True))



In [10]:
top_3_sorted

{1260: 748160.8925182365,
 32298: 48285.9857297699,
 33060: 45231.091694665905,
 32478: 34711.0794852282,
 32411: 28072.110667188208,
 32756: 27967.844298607495,
 32912: 26005.594662738444,
 31689: 22942.062086770176,
 33061: 21725.745716019766,
 7914: 18612.594734007733,
 32920: 17024.376791714127,
 21834: 16755.64974896288,
 13972: 16183.764447889904,
 33077: 15803.042613803402,
 19773: 15220.680084533069,
 33076: 14860.339807279099,
 33078: 14860.339807279099,
 32750: 13205.686481864266,
 10173: 11249.455347743986,
 32463: 10090.5329153237,
 33150: 9486.156008911714,
 32866: 9473.46662714043,
 23850: 9303.729931817254,
 23853: 8489.84364479469,
 33079: 8460.339807279106,
 32921: 8247.488593039916,
 9437: 8042.610529294726,
 33080: 8042.610529294726,
 33081: 8042.610529294726,
 33082: 8042.610529294726,
 32956: 7852.252883630921,
 32856: 7706.840793193316,
 32986: 7601.086545602344,
 4414: 7404.346182409335,
 32688: 7225.21068520549,
 32488: 7148.98713715086,
 26251: 6796.03233581593

**Input the value of Top-k Features**

In [25]:
#Extracting the top-k features for each class and perform the union operation to all the top-k features
k=int(input("Enter the value of k for selecting the top-k features"))
top_1_index=set()
top_2_index=set()
top_3_index=set()
top_4_index=set()
top_5_index=set()

count=1
for key,v in top_1_sorted.items():
 
  if(count>k):
    break
  top_1_index.add(key)
  count+=1

count=1
for key,v in top_2_sorted.items():
  
  if(count>k):
    break
  top_2_index.add(key)
  count+=1

count=1
for key,v in top_3_sorted.items():
  
  if(count>k):
    break
  top_3_index.add(key)
  count+=1

count=1
for key,v in top_4_sorted.items():
  
  if(count>k):
    break
  top_4_index.add(key)
  count+=1


count=1
for key,v in top_5_sorted.items():
  
  if(count>k):
    break
  top_5_index.add(key)
  count+=1

Enter the value of k for selecting the top-k features30


In [26]:
#Performing the union to all the top-k features for each class
top_index = top_1_index.union(top_2_index,top_3_index,top_4_index,top_5_index)

In [27]:
top_index = list(top_index)

In [28]:
#Converting the tf-icf matrix into the dataframe
df = pd.DataFrame(matrix_tf_icf)
df = df.iloc[:,top_index] # Select columns by Index


In [29]:
df

1      1281   21251  18434  4101   20998  46343  56887  21003  \
0     762.003801    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1     762.003801    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2     762.003801    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3     762.003801    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4     762.003801    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...          ...    ...    ...    ...    ...    ...    ...    ...    ...   
4995    0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4996    0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4997    0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4998    0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4999    0.000000    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

           50445  ...  1265         57070  39154  32756  2805        6388   \
0       0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
1       0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
2       0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
3       0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
4       0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
...          ...  ...    ...          ...    ...    ...    ...         ...   
4995    0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
4996  387.324932  ...    0.0  1256.163099    0.0    0.0    0.0    0.000000   
4997  387.324932  ...    0.0  1256.163099    0.0    0.0    0.0  147.764996   
4998    0.000000  ...    0.0     0.000000    0.0    0.0    0.0    0.000000   
4999  387.324932  ...    0.0  1256.163099    0.0    0.0    0.0    0.000000   

      46328  3067   16380  2303   
0       0.0    0.0    0.0    0.0  
1       0.0    0.0    0.0    0.0  
2       0.0    0.0    0.0    0.0  
3       0.0    0.0    0.0    0.0  
4       0.0    0.0    0.0    0.0  
...     ...    ...    ...    ...  
4995    0.0    0.0    0.0    0.0  
4996    0.0    0.0    0.0    0.0  
4997    0.0    0.0    0.0    0.0  
4998    0.0    0.0    0.0    0.0  
4999    0.0    0.0    0.0    0.0  

[5000 rows x 147 columns]

# **Naive Bayes Algorithm**

In [52]:
#Multinomial naive bayes class implementation
class MultiNB:
  def __init__(self):
    pass
# Prediction function
  def predict(self, x_test):
      pred=[self.custom_predict(x_test) for x_test in x_test]
      return pred
# Finding the prediction based on the posterior probability and likelihood
  def custom_predict(self, x_test):
      posterior_prob = list()
      for idx, c in enumerate(self._classes):
          temp=self._priors[idx]
          prio = np.log(temp)
          likelihood = self.likelihood_calculate(self._likelihoods[idx,:], x_test)
          s=np.sum(likelihood)
          posteriors_c = s + prio
          posterior_prob.append(posteriors_c)

      return self._classes[np.argmax(posterior_prob)]

# calculating the likelihood from the x-test
  def likelihood_calculate(self, cls_likeli, x_test):
      temp1=cls_likeli
      temp_p=np.log(temp1)
      return temp_p * x_test
# Implementing the fit operation on x-train and y-train to train the model
  def fit(self, x_train, y_train):
      m = x_train.shape[0]
      n = x_train.shape[1]
      self._classes = np.unique(y_train)
      n_classes = len(self._classes)

      self._priors = np.zeros(n_classes)
      self._likelihoods = np.zeros((n_classes, n))

      for index, cl in enumerate(self._classes):
          x_train_c = x_train[cl == y_train]
          self._priors[index] = x_train_c.shape[0] / m
          temp_sum=x_train_c.sum(axis=0)
          al=1 
          temp1=(temp_sum) + al
          temp2=np.sum(x_train_c.sum(axis=0) + al)
          temp3=temp1 / temp2
          self._likelihoods[index, :] = temp3

  


**Part 6.a) 50:50 split ratio**

In [53]:
#Splitting the dataset with k features into 50-50 ratio
X_train, X_test, y_train, y_test = train_test_split(df, file_content['label'], test_size=0.5, random_state=143)
nb=MultiNB()
nb.fit(np.array(X_train), np.array(y_train))
y_pred=nb.predict(np.array(X_test))
print(classification_report(y_pred,y_test))



              precision    recall  f1-score   support

           1       1.00      1.00      1.00       526
           2       1.00      1.00      1.00       505
           3       0.99      0.75      0.85       635
           4       0.83      0.99      0.90       403
           5       0.84      1.00      0.91       431

    accuracy                           0.93      2500
   macro avg       0.93      0.95      0.93      2500
weighted avg       0.94      0.93      0.93      2500



**Part 6.b) 70:30 split ratio**

In [54]:
#Splitting the dataset with k features into 70-30 ratio
X_train, X_test, y_train, y_test = train_test_split(df, file_content['label'], test_size=0.3, random_state=143)
nb=MultiNB()
nb.fit(np.array(X_train), np.array(y_train))
y_pred=nb.predict(np.array(X_test))
print(classification_report(y_pred,y_test))



              precision    recall  f1-score   support

           1       1.00      0.99      1.00       292
           2       1.00      1.00      1.00       301
           3       0.99      0.74      0.85       389
           4       0.81      0.99      0.89       239
           5       0.85      1.00      0.92       279

    accuracy                           0.93      1500
   macro avg       0.93      0.94      0.93      1500
weighted avg       0.94      0.93      0.93      1500



**Part 6.c) 80:20 split ratio**

In [55]:
#Splitting the dataset with k features into 80-20 ratio
X_train, X_test, y_train, y_test = train_test_split(df, file_content['label'], test_size=0.2, random_state=143)
nb=MultiNB()
nb.fit(np.array(X_train), np.array(y_train))
y_pred=nb.predict(np.array(X_test))
print(classification_report(y_pred,y_test))



              precision    recall  f1-score   support

           1       1.00      0.99      0.99       196
           2       1.00      1.00      1.00       210
           3       1.00      0.80      0.89       247
           4       0.80      0.82      0.81       174
           5       0.78      1.00      0.88       173

    accuracy                           0.92      1000
   macro avg       0.92      0.92      0.91      1000
weighted avg       0.93      0.92      0.92      1000

